# Overview 

<span style="color:red; font-size:18px; font-weight:bold;">In this notebook, we will try to create a workflow between Langchain and Mixtral LLM.</br>
We want to accomplish the following:</span>
1. Establish a pipeline to read in a csv and pass it to our LLM. 
2. Establish a Pandas Agent in our LLM.
3. Connect the CSV pipeline to this agent and enable a end-end EDA pipeline.

# Setting up the Environment 

In [1]:
####################################################################################################
import os
import re
import subprocess
import sys
from PIL import Image


from langchain import hub
from langchain.agents.agent_types import AgentType
from langchain_experimental.agents.agent_toolkits import create_pandas_dataframe_agent
from langchain_experimental.utilities import PythonREPL
from langchain.agents import Tool
from langchain.agents.format_scratchpad.openai_tools import (
    format_to_openai_tool_messages,
)
from langchain.agents.output_parsers.openai_tools import OpenAIToolsAgentOutputParser

from langchain.agents import AgentExecutor

from langchain.agents import create_structured_chat_agent
from langchain.memory import ConversationBufferWindowMemory

from langchain.output_parsers import PandasDataFrameOutputParser
from langchain.prompts import PromptTemplate

from langchain_core.prompts import ChatPromptTemplate, MessagesPlaceholder

from langchain_community.chat_models import ChatAnyscale
import pandas as pd 
import matplotlib.pyplot as plt 
import numpy as np

plt.style.use('ggplot')
####################################################################################################

In [2]:
# insert your API key here
os.environ["ANYSCALE_API_KEY"] = "esecret_8btufnh3615vnbpd924s1t3q7p"
memory_key = "history"

# Using out of the box agents
<span style="font-size:16px;color:red;"> Over here we simply try to run the Pandas Dataframe agent provided by langchain out of the box. It uses a CSV parser and has just one tool, the __PythonAstREPLTool__ which helps it execute python commands in a shell and display output. </span>

# DECLARE YOUR LLM HERE 

# Building my own DF chain
<span style="font-size:16px;color:red"> The above agent does not work well or mistral out of the box. The mistral LLM is unable to use the tools properly. It perhaps needs much more hand-held prompts.</span>

### Post Implementation Observation:
<span style="font-size:16px;color:red"> We were able to observe the following:</br>
    1. The agent now works very well almost always returning the desired output.</br>
    2. The agent is unable to output plots. </span>

# Building an Agent 

In [4]:
prompt = ChatPromptTemplate.from_messages(
    [
        (
            "system",
            f"""You are Data Analysis assistant. Your job is to use your tools to answer a user query in the best\
            manner possible. Your job is to respond to user queries by generating a python code file.\
            Make sure to include all necessary imports.\
            In case you make plots, make sure to label the axes and add a good title too. \
            You must save any plots in the 'graphs' folder as png only.\
            Provide no explanation for your code.\
            Read the data from 'df.csv'.\
            ** Enclose all your code between triple backticks ``` **\
            RECTIFY ANY ERRORS FROM THE PREVIOUS RUNS.
            """,
        ),
        ("user", "Dataframe named df: {df}\nQuery: {input}\nTools:{tools}"),
        MessagesPlaceholder(variable_name="agent_scratchpad"),
    ]
)

In [5]:
python_repl = PythonREPL()

repl_tool = Tool(
    name="python_repl",
    description="""A Python shell. Shell can dislay charts too. Use this to execute python commands.\
    You have access to all libraries in python including but not limited to sklearn, pandas, numpy,\
    matplotlib.pyplot, seaborn etc. Input should be a valid python command. If the user has not explicitly\
    asked you to plot the results, always print the final output using print(...)""",
    func=python_repl.run,
)

if 'code' not in os.listdir():
    os.mkdir('code')
    
tools = [repl_tool]

In [6]:
def delete_png_files(dir_path):
    for filename in os.listdir(dir_path):
        if filename.endswith(".png"):
            os.remove(os.path.join(dir_path, filename))

In [7]:
def run_code(code):
    
    with open(f'{os.getcwd()}/code/code.py', 'w') as file:
        file.write(code)
        
    try:
        print("Running code ...\n")
        result = subprocess.run([sys.executable, 'code/code.py'], capture_output=True, text=True, check=True, timeout=20)
        return result.stdout, False
    
    except subprocess.CalledProcessError as e:
        print("Error in code!\n")
        return e.stdout + e.stderr, True
    
    except subprocess.TimeoutExpired:
        return "Execution timed out.", True

In [8]:
def infer_EDA(user_input:str = ''):    
    agent = (
            {
                "input": lambda x: x["input"],
                "tools": lambda x:x['tools'],
                "df": lambda x:x['df'],
                "agent_scratchpad": lambda x: format_to_openai_tool_messages(
                    x["intermediate_steps"]
                )
            }
            | prompt
            | llm
            | OpenAIToolsAgentOutputParser()
        )

    EDA_executor = AgentExecutor(agent=agent, tools=tools, df = 'df.csv', verbose=True)
    
    # Running Inference
    error_flag = True
    image_path = f'{os.getcwd()}/graphs'
    
    delete_png_files(image_path)
    res = None
    
    while error_flag:
        result = list(EDA_executor.stream({"input": user_input, 
                                     "df":pd.read_csv('df.csv'),
                                     "tools":tools}))

        # need to extract the code
        pattern = r"```python\n(.*?)\n```"
        matches = re.findall(pattern, result[0]['output'], re.DOTALL)
        code = "import matplotlib\nmatplotlib.use('Agg')\n"
        code += "\n".join(matches)

        # execute the code
        res, error_flag = run_code(code)
    
    image = None
    
    for file in os.listdir(image_path):
        if file.endswith(".png"):
            image = np.array(Image.open(f'{image_path}/{file}'))
            break
    
    final_val = result[-1]['output'] + f'\n{res}'
    
    return final_val , image

In [9]:
def run_agent(data_path:str = '', provider:str = 'Mistral', agent_type:str = 'EDA', query:str = '', layers:str ='', temp:float = 0.1):
    
    df = pd.read_csv(data_path)
    df.to_csv('./df.csv', index=False)
    
    if provider.lower() == 'mistral':
        
        llm = ChatAnyscale(model_name='mistralai/Mixtral-8x7B-Instruct-v0.1', temperature=temp)
        
        if agent_type == 'Data Explorer':
            EDA_response, EDA_image = infer_EDA(user_input=query)
            return EDA_response, EDA_image
        
    return None

# Gradio Demo

In [10]:
import gradio as gr

demo = gr.Interface (
    run_agent,
    [
        gr.UploadButton(label="Upload your CSV!"),
        gr.Radio(["Mistral","GPT"],label="Select Your LLM"),
        gr.Radio(["Data Explorer", "Hypothesis Tester", "Basic Inference", "Super Inference"], label="Choose Your Agent"),
        gr.Text(label="Query", info="Your input to the Agent"),
        gr.Text(label="Architecture", info="Specify the layer by layer architecture only for Super Inference Agent"),
        gr.Slider(label="Model Temperature", info="Slide right to make your model more creative!")
    ],
    [
        gr.Text(label="Updated JSON Object", info="This the JSON Object with the changed component."),
        gr.Image(label="Graph")
    ]
)
demo.launch(share=True)

Running on local URL:  http://127.0.0.1:7860

Could not create share link. Please check your internet connection or our status page: https://status.gradio.app.




> Entering new AgentExecutor chain...
 ```python
import pandas as pd
import numpy as np

# Read the data from 'df.csv'
df = pd.read_csv('df.csv')

# Calculate the number of null values in each column
null_counts = df.isnull().sum()

# Calculate the total number of null values in the dataframe
total_null_count = df.isnull().sum().sum()

# Print the distribution of null values in the dataframe
print("Null Value Distribution:")
print(null_counts)
print(f"Total Null Count: {total_null_count}")
```

> Finished chain.
Running code ...



> Entering new AgentExecutor chain...
 ```python
import pandas as pd
import matplotlib.pyplot as plt

# Read the data from 'df.csv'
df = pd.read_csv('df.csv')

# Calculate the number of null values in each column
null_counts = df.isnull().sum()

# Prepare data for plotting
data = null_counts.sort_values(ascending=False)

# Create a bar plot of null values distribution
plt.figure(figsize=(10, 6))
plt.bar(data.index, data.values)
plt.title('Distribution of N